In [1]:
import transformers
import torch
import numpy as np

In [2]:
from peft import PeftConfig, PeftModel
from transformers import AutoModelForCausalLM, AutoTokenizer

base_model_name = "meta-llama/Llama-3.2-1B"
adapter_model_name = "outputs/checkpoint-92000"

model = AutoModelForCausalLM.from_pretrained(base_model_name)
model = PeftModel.from_pretrained(model, adapter_model_name)

tokenizer = AutoTokenizer.from_pretrained(base_model_name)

In [3]:
id2token = tokenizer.convert_ids_to_tokens(list(range(tokenizer.vocab_size)))

In [4]:
id2string = []
for token in id2token:
    id2string.append(tokenizer.convert_tokens_to_string([token]))

In [11]:
inputs = tokenizer("""Translate Natural Language into CQL Queries
What is Corpus Query Language (CQL)?

Corpus Query Language (CQL) is a formal query syntax used to search linguistic corpora for complex patterns that involve words, lemmas, part-of-speech tags, and other annotations. CQL enables users to define conditions on individual tokens or sequences of tokens using features like:

Square bracket notation for token features:

Word dog followed by lemma run and then followed by a noun. CQL:
```
[word="dog"][lemma="run"][pos="NN"]
```

Regular expression-like syntax:

An adjective followed by a noun. CQL:
```
[pos="JJ"][pos="NN"]
```

Lemma "be" optionaly followed by word "not". CQL:
```
[lemma="be"][word="not"]? 
```

Answer in a code block (Line enclosed with ```). Write only CQL into the code blocks.

Translate: """ + """Any word followed by a noun within a sentence.""" " CQL:\n```\n", return_tensors="pt")
outputs = model.generate(**inputs, max_new_tokens=100)
result = tokenizer.decode(outputs[0], skip_special_tokens=True)
result_cql = result.split("Translate: ", 1)[1].split("```")[1]
print(result_cql)

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.



[word="any"][word="of"][plural=[pos="NN"][singular="[pos="PP"]"][relation="IN"]][relation="that"][word="do"][pos="VVG"]

